In [ ]:
import numpy as np
import pylab as plt

import networkx as nx
import random as rand

# Continuous Action space and Deterministic gradient Policy

The previous algorithm can be used only for **discrete action space**.
For the control of **ODE/PDE** of for other applications it will be interesting to deal with **continuous action space**

The Bellman optimality equation and the theory is the same as for the continuous state space and discrete action space. However some operator as $\operatorname{max}_{\mathbf{a}}$ are difficult to estimate in practice.

In the following we will introduce an algorithm based on the actor/critic approach ablle to deal with continuous action space.

Firstly we will introduce the **policy grandient theorem** in this case.

In the following we will introduce deterministic gradient policy **DPG**. 

There is a crucial difference between
the stochastic and deterministic policy gradients. In
the stochastic case, the policy gradient integrates over both
state and action spaces, whereas in the deterministic case it
only integrates over the state space. 

Computing
the stochastic policy gradient may require more examples for high dimensional action space.

However the exploratory part is essential in these algorithms. In practice **off policy** method are used where we construct a stochastic behavior/exploratory policy using the **deterministic one + a random noise**. At the end it use a stochastic policy for exploration but a deterministic one for learning.


In the continuous state and action case the policy gradient theorem. To we begin we define the reward functional:

$$
\mathcal{J}(\theta)= \int_S d^{\pi_{\theta}}(\mathbf{s})V^{\pi_{\theta}}(\mathbf{s})=\int_{S} d^{\pi_{\theta}}(\mathbf{s})\int_A \pi_{\theta}(\mathbf{a}\mid \mathbf{s})Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a})d \mathbf{a}d \mathbf{s}
$$

So the **Gradient policy theorem** for the continuous action/state space is given by:

$$
\nabla_{\theta}\mathcal{J}(\theta) = \int_{S} d^{\pi_{\theta}}(\mathbf{s})\int_A Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a})\nabla_{\theta}\pi_{\theta}(\mathbf{a}\mid \mathbf{s})d \mathbf{a}d \mathbf{s}
$$

Using this theorem we can design **Stochastic Actor/critic algorithms** for the continuous state/action case. In practice it is not easy/possible to construct a neural network describing the continuous probability distribution for the stochastic policy. However it is preferable to introduce a **deterministic policy**.

**Definition**: *we note $\mu(\mathbf{s})$ the deterministic policy*.

In the deterministic case we consider the following functionnal

$$
\mathcal{J}(\theta)= \int_S d^{\nu_{\theta}}(\mathbf{s})V^{\nu_{\theta}}(\mathbf{s})=\int_{S} d^{\pi_{\theta}}(\mathbf{s}) Q^{\mu_{\theta}}(\mathbf{s},\mu_{\theta}(\mathbf{s}))d \mathbf{s} = \mathbf{E}_{\mu_{\theta}}[Q^{\mu_{\theta}}(\mathbf{s},\mu_{\theta}(\mathbf{s}))]
$$

In a fully deterministic case $d^{\nu_{\theta}}$ is a uniform law.

Using the chain rules we obtain:

$$
\nabla_{\theta}\mathcal{J}(\theta)=\int_{S} d^{\pi_{\theta}}(\mathbf{s}) \nabla_{\theta}Q^{\mu_{\theta}}(\mathbf{s},\mu_{\theta}(\mathbf{s}))d \mathbf{s} = \int_{S} d^{\pi_{\theta}}(\mathbf{s}) \nabla_{\theta} \mu(\mathbf{s}) [\nabla_{a}Q^{\mu_{\theta}}](\mathbf{s},\mu_{\theta}(\mathbf{s})) d \mathbf{s} = \mathbf{E}_{\mu_{\theta}}[\nabla_{\theta} \mu(\mathbf{s}) [\nabla_{a}Q^{\mu_{\theta}}](\mathbf{s},\mu_{\theta}(\mathbf{s}))]]
$$

## DPPG algorithm

https://lilianweng.github.io/lil-log/2018/04/08/policy-gradient-algorithms.html#off-policy-policy-gradient

https://spinningup.openai.com/en/latest/algorithms/ddpg.html

https://towardsdatascience.com/deep-deterministic-policy-gradients-explained-2d94655a9b7b

https://hal.inria.fr/hal-00938992

https://arxiv.org/abs/1509.02971

The DDPG algorithm consist to compute the previous gradient using some ingredients:
- compute the gradient using **Monte-Carlo method** (empirical average),
- update the policy using the gradient computed,
- Neural Network for the policy and the Q function (regression in the two cases).
- The Q function is update using the Q-learning principle,
- experience replay and periodical update of the target ( as Deep Q learning),
- partially random exploration,

The ingredients one and two correspond to

$$
\nabla_{\theta}\mathcal{J}(\theta) = \mathbf{E}_{\mu_{\theta}}[\nabla_{\theta} \mu(\mathbf{s}) [\nabla_{a}Q^{\mu_{\theta}}](\mathbf{s},\mu_{\theta}(\mathbf{s}))]] \approx \frac{1}{M}\sum_{i=0}^M \nabla_{\theta} \mu(\mathbf{s}_i) [\nabla_{a}Q^{\mu_{\theta}}](\mathbf{s}_i,\mu_{\theta}(\mathbf{s}_i))
$$

and the weights of the ANN are updated with a gradient descent using the previous gradient.

The update of the Q function is based on the Q-learning. Wo we sue a regression with the following loss:

$$
\frac{1}{M}\sum_{i=0}^M (\mathbf{y}_i - Q_{\theta}(\mathbf{s}_i,\mathbf{a}_i))^2
$$

with $\mathbf{y}_i =\mathbf{r}_i + \gamma Q_{\theta}(\mathbf{s}_{i+1},\mu_{\theta}(\mathbf{s}_{i+1}))$.

Coupling with experience replay, periodically update the target and random exploeration we obtain the followi

- Initialize $\theta^{Q}, \theta^{\mu}$ arbitrarly
- Initialize $\theta^{Q^{'}}, \theta^{\mu^{'}}$ arbitrarly
- for all the episodes $k$: 1 to $N$:
 - choose randomly a initial state $\mathbf{s}_0$
 - choose a random process $\mathcal{N}$
 - such that $\mathbf{s}_t$ is terminal:
     - choose an action $\mathbf{a}_{t}=\mu_{\theta^{\mu}}(\mathbf{s}_t)+\mathcal{N}$ 
     - execute action $\mathbf{a}_t$ and observe $\mathbf{r}_t$ and $\mathbf{s}_{t+1}$
     - store the transition in $(\mathbf{s}_t,\mathbf{a}_t,\mathbf{r}_{t+1},\mathbf{s}_{t+1})$ in D
     - sample a random minibatch $(\mathbf{s}_i,\mathbf{a}_i,\mathbf{r}_{i+1},\mathbf{s}_{i+1})$ on size N in the memory D
     
     - compute the reference solution for the regression:
     
     $$
     \mathbf{y}_i = \left\{\begin{array}{l} \mathbf{r}_{i+1} \mbox{ if $\mathbf{s}_i$ is terminal}\\
     \mathbf{r}_{i+1} + \gamma Q_{\theta^{Q^{'}}}(\mathbf{s}_{i+1},\mu_{\theta^{\mu^{'}}}(\mathbf{s}_{i+1})) \mbox{ else }
     \end{array}\right. 
     $$
     
     - update the critic using the loss:
     
     $$
     \frac{1}{N}\sum_{i=0}^N (\mathbf{y}_i - Q_{\theta^{Q}}(\mathbf{s}_i,\mathbf{a}_i))^2
     $$
     
     - update the actor using the sample gradient:
     
     $$
     \frac{1}{N}\sum_{i=0}^N \nabla_{\theta} \mu_{\theta^{\mu}}(\mathbf{s}_i) [\nabla_{a}Q_{\theta^{Q}}](\mathbf{s}_i,\mu_{\theta^{\mu}}(\mathbf{s}_i))
     $$
     
     - update the target network with the weights
     
     $$
     \theta^{Q^{'}} := \tau \theta^{Q^{'}} +(1-\tau)\theta^{Q}, \quad \theta^{\mu^{'}} := \tau \theta^{\mu^{'}} +(1-\tau)\theta^{\mu}
     $$